In [55]:
import pandas as pd
import zipfile
import geopandas as gpd
import fiona
import folium
import os

## Import Data

In [5]:
data = pd.read_csv("data/KingCountyHousingData.csv", index_col = 0)

In [6]:
data.head()

Major  Minor  ZipCode DocumentDate  SalePrice  SqFtLot  SqFtTotLiving  \
0    100     67    98002   2019-04-01     310800    17400           2240   
1    100     66    98002   2019-10-22     339000    14500           1200   
2    100     42    98002   2019-10-29     485500     6002           2134   
3    120      8    98166   2019-05-17     850000    24142           3500   
4    140     27    98178   2019-05-28     535000    14208           2170   

       Nuisances  Has_Nuisance  TrafficNoise  ...  View_Cascades  \
0   No Nuisances             0             0  ...              0   
1   No Nuisances             0             0  ...              0   
2   No Nuisances             0             0  ...              0   
3   No Nuisances             0             0  ...              0   
4  Traffic Noise             1             1  ...              0   

   SeattleSkyline  View_PugetSound View_LakeWashington  View_LakeSammamish  \
0               0                0                   0                   0   
1               0                0                   0                   0   
2               0                0                   0                   0   
3               0                0                   0                   0   
4               0                0                   0                   0   

   View_SmallLakeRiverCreek  BldgGrade  Has_Deck  Has_Finished_Basement  \
0                         0        6.0         0                      0   
1                         0        5.0         0                      0   
2                         0        5.0         0                      0   
3                         0        6.0         1                      1   
4                         0        5.0         1                      1   

   Has_Attached_Garage  
0                    1  
1                    1  
2                    1  
3                    0  
4                    0  

[5 rows x 29 columns]

In [7]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 27786 entries, 0 to 27785
Data columns (total 29 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   Major                     27786 non-null  int64  
 1   Minor                     27786 non-null  int64  
 2   ZipCode                   27786 non-null  int64  
 3   DocumentDate              27786 non-null  object 
 4   SalePrice                 27786 non-null  int64  
 5   SqFtLot                   27786 non-null  int64  
 6   SqFtTotLiving             27786 non-null  int64  
 7   Nuisances                 27786 non-null  object 
 8   Has_Nuisance              27786 non-null  int64  
 9   TrafficNoise              27786 non-null  int64  
 10  PowerLines                27786 non-null  int64  
 11  OtherNuisances            27786 non-null  int64  
 12  Is_WaterFrontLocation     27786 non-null  int64  
 13  WaterFrontLocation        27786 non-null  object 
 14  Has_Po

In [42]:
# Create data frame that include only data needed for map

df_map = data[['ZipCode', 'SalePrice']]
df_map

ZipCode  SalePrice
0        98002     310800
1        98002     339000
2        98002     485500
3        98166     850000
4        98178     535000
...        ...        ...
27781    98033    3125000
27782    98055     245000
27783    98166    1275000
27784    98166     435000
27785    98125     650000

[27786 rows x 2 columns]

In [43]:
df_map['SalePrice'].max()

10050000

In [44]:
# Sort by ZipCode

df_map = df_map.sort_values('ZipCode')

In [45]:
df_map_mean = df_map.groupby('ZipCode').mean()
df_map_mean.head(20)

SalePrice
ZipCode              
89045    1.032976e+06
91844    8.200000e+05
95059    7.378429e+05
98001    4.406618e+05
98002    4.052143e+05
98003    4.621811e+05
98004    2.412158e+06
98005    1.279316e+06
98006    1.186221e+06
98007    8.811987e+05
98008    1.032914e+06
98010    7.317934e+05
98011    7.841755e+05
98012    5.149500e+05
98013    5.354500e+05
98014    7.512878e+05
98018    4.499500e+05
98019    6.685382e+05
98022    4.987765e+05
98023    4.366385e+05

In [46]:
df_map_mean.at[98022, 'SalePrice']

498776.5171717172

In [47]:
df_map_mean.index.name = 'ZIPCODE'
df_map_mean

SalePrice
ZIPCODE              
89045    1.032976e+06
91844    8.200000e+05
95059    7.378429e+05
98001    4.406618e+05
98002    4.052143e+05
...               ...
98288    2.564433e+05
98302    8.062417e+05
98354    3.860030e+05
98405    8.958280e+05
98812    7.275000e+05

[91 rows x 1 columns]

In [48]:
df_map_mean = df_map_mean.reset_index()
df_map_mean

ZIPCODE     SalePrice
0     89045  1.032976e+06
1     91844  8.200000e+05
2     95059  7.378429e+05
3     98001  4.406618e+05
4     98002  4.052143e+05
..      ...           ...
86    98288  2.564433e+05
87    98302  8.062417e+05
88    98354  3.860030e+05
89    98405  8.958280e+05
90    98812  7.275000e+05

[91 rows x 2 columns]

In [49]:
exclude_zipcode = [89045, 91844, 95059, 98012, 98321, 98354, 98405]

In [50]:
df_map_mean1 = df_map_mean[~df_map_mean.isin(exclude_zipcode)]
df_map_mean = df_map_mean1.dropna()

In [51]:
df_map_mean

ZIPCODE     SalePrice
3   98001.0  4.406618e+05
4   98002.0  4.052143e+05
5   98003.0  4.621811e+05
6   98004.0  2.412158e+06
7   98005.0  1.279316e+06
..      ...           ...
84  98199.0  1.129775e+06
85  98224.0  3.204833e+05
86  98288.0  2.564433e+05
87  98302.0  8.062417e+05
90  98812.0  7.275000e+05

[85 rows x 2 columns]

In [52]:
len(df_map_mean)

85

### Import Geometry

In [14]:
! wget -P data https://opendata.arcgis.com/datasets/83fc2e72903343aabff6de8cb445b81c_2.zip

--2021-01-28 18:50:08--  https://opendata.arcgis.com/datasets/83fc2e72903343aabff6de8cb445b81c_2.zip
Resolving opendata.arcgis.com (opendata.arcgis.com)... 3.211.162.230, 52.4.203.140, 3.210.242.135, ...
Connecting to opendata.arcgis.com (opendata.arcgis.com)|3.211.162.230|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [application/zip]
Saving to: ‘data/83fc2e72903343aabff6de8cb445b81c_2.zip’

83fc2e72903343aabff     [         <=>        ]   4.68M   664KB/s    in 11s     

2021-01-28 18:50:21 (452 KB/s) - ‘data/83fc2e72903343aabff6de8cb445b81c_2.zip’ saved [4904244]



In [16]:
with zipfile.ZipFile('data/83fc2e72903343aabff6de8cb445b81c_2.zip', 'r') as zip_ref:
    zip_ref.extractall('data')

In [24]:
df_zipcode = gpd.read_file('data/Zip_Codes.shp')
df_zipcode

OBJECTID    ZIP ZIPCODE COUNTY     SHAPE_Leng    SHAPE_Area  \
0           1  98031   98031    033  117508.211718  2.280129e+08   
1           2  98032   98032    033  166737.664791  4.826754e+08   
2           3  98033   98033    033  101363.840369  2.566747e+08   
3           4  98034   98034    033   98550.452509  2.725072e+08   
4           5  98030   98030    033   94351.264837  2.000954e+08   
..        ...    ...     ...    ...            ...           ...   
199       200  98402   98402    053   30734.178112  2.612224e+07   
200       201  98403   98403    053   23495.038425  2.890938e+07   
201       202  98404   98404    053   61572.154365  2.160645e+08   
202       203  98405   98405    053   50261.100559  1.193118e+08   
203       204  98406   98406    053   74118.972418  1.088373e+08   

                                              geometry  
0    POLYGON ((-122.21842 47.43750, -122.21935 47.4...  
1    MULTIPOLYGON (((-122.24187 47.44122, -122.2411...  
2    POLYGON ((-122.20571 47.65170, -122.20511 47.6...  
3    POLYGON ((-122.17551 47.73706, -122.17554 47.7...  
4    POLYGON ((-122.16746 47.38549, -122.16746 47.3...  
..                                                 ...  
199  POLYGON ((-122.44279 47.26479, -122.44272 47.2...  
200  POLYGON ((-122.44382 47.26617, -122.44434 47.2...  
201  POLYGON ((-122.38900 47.23495, -122.38932 47.2...  
202  POLYGON ((-122.44092 47.23639, -122.44944 47.2...  
203  MULTIPOLYGON (((-122.52125 47.27121, -122.5191...  

[204 rows x 7 columns]

In [25]:
df_zipcode = df_zipcode.sort_values('ZIPCODE')
df_zipcode

OBJECTID    ZIP ZIPCODE COUNTY     SHAPE_Leng    SHAPE_Area  \
42         43  98001   98001    033  156155.466031  5.324255e+08   
41         42  98002   98002    033  102448.491014  2.055688e+08   
40         41  98003   98003    033  120498.920879  3.170769e+08   
39         40  98004   98004    033  108762.980060  2.014501e+08   
38         39  98005   98005    033  116409.338330  2.113641e+08   
..        ...    ...     ...    ...            ...           ...   
175       176  98940   98940    037  465055.060878  5.451150e+09   
176       177  98941   98941    037  128017.064125  3.570243e+08   
177       178  98943   98943    037   14265.719129  1.006428e+07   
198       199  98946   98946    037  148179.572121  8.366639e+08   
179       180  98950   98950    037  209701.376911  9.157248e+08   

                                              geometry  
42   POLYGON ((-122.22992 47.35377, -122.22993 47.3...  
41   POLYGON ((-122.22921 47.35375, -122.22915 47.3...  
40   POLYGON ((-122.30960 47.35795, -122.30940 47.3...  
39   MULTIPOLYGON (((-122.21458 47.65298, -122.2146...  
38   POLYGON ((-122.15876 47.66065, -122.15839 47.6...  
..                                                 ...  
175  POLYGON ((-121.11377 47.59713, -121.11374 47.5...  
176  POLYGON ((-121.00593 47.23316, -120.96324 47.2...  
177  POLYGON ((-120.94261 47.18516, -120.94232 47.1...  
198  POLYGON ((-120.81410 47.04108, -120.81469 47.1...  
179  POLYGON ((-119.99940 46.73773, -119.99789 46.8...  

[204 rows x 7 columns]

In [26]:
df_zipcode['ZIPCODE'] = df_zipcode['ZIPCODE'].astype(int)

In [27]:
df_zipcode.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Int64Index: 204 entries, 42 to 179
Data columns (total 7 columns):
 #   Column      Non-Null Count  Dtype   
---  ------      --------------  -----   
 0   OBJECTID    204 non-null    int64   
 1   ZIP         204 non-null    int64   
 2   ZIPCODE     204 non-null    int64   
 3   COUNTY      203 non-null    object  
 4   SHAPE_Leng  204 non-null    float64 
 5   SHAPE_Area  204 non-null    float64 
 6   geometry    204 non-null    geometry
dtypes: float64(2), geometry(1), int64(3), object(1)
memory usage: 12.8+ KB


In [53]:
df_map_choropleth = df_zipcode.merge(df_map_mean, on='ZIPCODE')
df_map_choropleth

OBJECTID    ZIP  ZIPCODE COUNTY     SHAPE_Leng    SHAPE_Area  \
0         43  98001    98001    033  156155.466031  5.324255e+08   
1         42  98002    98002    033  102448.491014  2.055688e+08   
2         41  98003    98003    033  120498.920879  3.170769e+08   
3         40  98004    98004    033  108762.980060  2.014501e+08   
4         39  98005    98005    033  116409.338330  2.113641e+08   
..       ...    ...      ...    ...            ...           ...   
77       128  98188    98188    033   94574.318151  2.187023e+08   
78        96  98198    98198    033  124157.387829  2.108446e+08   
79       100  98199    98199    033   56826.422800  1.145346e+08   
80       108  98224    98224    033  187335.038586  1.720745e+09   
81       125  98288    98288    033  484750.179357  8.748980e+09   

                                             geometry     SalePrice  
0   POLYGON ((-122.22992 47.35377, -122.22993 47.3...  4.406618e+05  
1   POLYGON ((-122.22921 47.35375, -122.22915 47.3...  4.052143e+05  
2   POLYGON ((-122.30960 47.35795, -122.30940 47.3...  4.621811e+05  
3   MULTIPOLYGON (((-122.21458 47.65298, -122.2146...  2.412158e+06  
4   POLYGON ((-122.15876 47.66065, -122.15839 47.6...  1.279316e+06  
..                                                ...           ...  
77  POLYGON ((-122.24187 47.44122, -122.24363 47.4...  4.769136e+05  
78  POLYGON ((-122.31456 47.42438, -122.31454 47.4...  4.693820e+05  
79  MULTIPOLYGON (((-122.40912 47.67160, -122.4089...  1.129775e+06  
80  POLYGON ((-121.34607 47.77992, -121.34587 47.7...  3.204833e+05  
81  POLYGON ((-121.11918 47.77994, -121.11918 47.7...  2.564433e+05  

[82 rows x 8 columns]

In [54]:
df_map_choropleth.sort_values('ZIPCODE')

OBJECTID    ZIP  ZIPCODE COUNTY     SHAPE_Leng    SHAPE_Area  \
0         43  98001    98001    033  156155.466031  5.324255e+08   
1         42  98002    98002    033  102448.491014  2.055688e+08   
2         41  98003    98003    033  120498.920879  3.170769e+08   
3         40  98004    98004    033  108762.980060  2.014501e+08   
4         39  98005    98005    033  116409.338330  2.113641e+08   
..       ...    ...      ...    ...            ...           ...   
77       128  98188    98188    033   94574.318151  2.187023e+08   
78        96  98198    98198    033  124157.387829  2.108446e+08   
79       100  98199    98199    033   56826.422800  1.145346e+08   
80       108  98224    98224    033  187335.038586  1.720745e+09   
81       125  98288    98288    033  484750.179357  8.748980e+09   

                                             geometry     SalePrice  
0   POLYGON ((-122.22992 47.35377, -122.22993 47.3...  4.406618e+05  
1   POLYGON ((-122.22921 47.35375, -122.22915 47.3...  4.052143e+05  
2   POLYGON ((-122.30960 47.35795, -122.30940 47.3...  4.621811e+05  
3   MULTIPOLYGON (((-122.21458 47.65298, -122.2146...  2.412158e+06  
4   POLYGON ((-122.15876 47.66065, -122.15839 47.6...  1.279316e+06  
..                                                ...           ...  
77  POLYGON ((-122.24187 47.44122, -122.24363 47.4...  4.769136e+05  
78  POLYGON ((-122.31456 47.42438, -122.31454 47.4...  4.693820e+05  
79  MULTIPOLYGON (((-122.40912 47.67160, -122.4089...  1.129775e+06  
80  POLYGON ((-121.34607 47.77992, -121.34587 47.7...  3.204833e+05  
81  POLYGON ((-121.11918 47.77994, -121.11918 47.7...  2.564433e+05  

[82 rows x 8 columns]

### Import Folium Map

In [56]:
# King County coordinates

coordinates = [47.5480, -121.9836]
# 47.5480° N, 121.9836° W
kc_latitude = coordinates[0]
kc_longitude = coordinates[1]

In [57]:
# Create map object

King_County_WA_map = folium.Map([kc_latitude, kc_longitude])
King_County_WA_map

In [58]:
# Create .geojson file

df_map_choropleth.to_file("zipcode_map.geojson", driver='GeoJSON')

In [59]:
# Access the .geojson file

overlay = os.path.join('zipcode_map.geojson')

In [60]:
tooltip_text = []
for i in range(len(df_map_choropleth)):
    tooltip_text.append('$' + str(round(df_map_choropleth['SalePrice'][i], 2)))
tooltip_text
   

['$440661.78',
 '$405214.32',
 '$462181.06',
 '$2412158.48',
 '$1279315.98',
 '$1186220.86',
 '$881198.74',
 '$1032913.52',
 '$731793.35',
 '$784175.5',
 '$751287.78',
 '$668538.19',
 '$498776.52',
 '$498776.52',
 '$436638.47',
 '$871451.08',
 '$950508.68',
 '$732189.63',
 '$887985.89',
 '$472091.29',
 '$521317.1',
 '$413450.89',
 '$1358330.63',
 '$869760.36',
 '$527065.87',
 '$3387976.46',
 '$1844477.4',
 '$513316.34',
 '$732822.16',
 '$442415.82',
 '$442415.82',
 '$603274.98',
 '$994627.13',
 '$1015374.15',
 '$494088.46',
 '$810408.23',
 '$488394.05',
 '$571143.82',
 '$721814.08',
 '$749373.8',
 '$703894.6',
 '$627605.86',
 '$914997.25',
 '$914997.25',
 '$1029695.59',
 '$1140630.61',
 '$1019220.4',
 '$1019220.4',
 '$570295.45',
 '$570295.45',
 '$1194397.77',
 '$864971.37',
 '$1216033.66',
 '$557483.82',
 '$875821.21',
 '$679613.34',
 '$1250265.41',
 '$1501551.43',
 '$938065.91',
 '$938576.53',
 '$858821.5',
 '$674385.93',
 '$1202825.85',
 '$947156.29',
 '$730171.28',
 '$656417.52',
 

In [61]:
type(tooltip_text)

list

In [62]:
df_map_choropleth = df_map_choropleth.assign(C=tooltip_text)
df_map_choropleth

OBJECTID    ZIP  ZIPCODE COUNTY     SHAPE_Leng    SHAPE_Area  \
0         43  98001    98001    033  156155.466031  5.324255e+08   
1         42  98002    98002    033  102448.491014  2.055688e+08   
2         41  98003    98003    033  120498.920879  3.170769e+08   
3         40  98004    98004    033  108762.980060  2.014501e+08   
4         39  98005    98005    033  116409.338330  2.113641e+08   
..       ...    ...      ...    ...            ...           ...   
77       128  98188    98188    033   94574.318151  2.187023e+08   
78        96  98198    98198    033  124157.387829  2.108446e+08   
79       100  98199    98199    033   56826.422800  1.145346e+08   
80       108  98224    98224    033  187335.038586  1.720745e+09   
81       125  98288    98288    033  484750.179357  8.748980e+09   

                                             geometry     SalePrice  \
0   POLYGON ((-122.22992 47.35377, -122.22993 47.3...  4.406618e+05   
1   POLYGON ((-122.22921 47.35375, -122.22915 47.3...  4.052143e+05   
2   POLYGON ((-122.30960 47.35795, -122.30940 47.3...  4.621811e+05   
3   MULTIPOLYGON (((-122.21458 47.65298, -122.2146...  2.412158e+06   
4   POLYGON ((-122.15876 47.66065, -122.15839 47.6...  1.279316e+06   
..                                                ...           ...   
77  POLYGON ((-122.24187 47.44122, -122.24363 47.4...  4.769136e+05   
78  POLYGON ((-122.31456 47.42438, -122.31454 47.4...  4.693820e+05   
79  MULTIPOLYGON (((-122.40912 47.67160, -122.4089...  1.129775e+06   
80  POLYGON ((-121.34607 47.77992, -121.34587 47.7...  3.204833e+05   
81  POLYGON ((-121.11918 47.77994, -121.11918 47.7...  2.564433e+05   

              C  
0    $440661.78  
1    $405214.32  
2    $462181.06  
3   $2412158.48  
4   $1279315.98  
..          ...  
77    $476913.6  
78   $469381.96  
79  $1129775.26  
80   $320483.33  
81   $256443.26  

[82 rows x 9 columns]

In [64]:
KC_WA_map = folium.Map([kc_latitude, kc_longitude])

choropleth = folium.Choropleth(
    geo_data=overlay, 
    #name='choropleth',
    data=df_map_choropleth,
    columns=('ZIPCODE', 'SalePrice'),
    key_on='feature.properties.ZIPCODE',
    fill_color='YlOrBr',
    fill_opacity=0.8,
    nan_fill_color='black',
    nan_fill_opacity=0.4,
    #line_weight=2,
    line_opacity=0.2,
    legend_name='Sale Price per ZipCode in King County, WA',
    highlight=True,
    reset=True
).add_to(KC_WA_map)

folium.LayerControl().add_to(KC_WA_map)


# Display Region Label
choropleth.geojson.add_child(folium.features.GeoJsonTooltip(['ZIPCODE', 'C'], labels=False))


In [53]:
KC_WA_map

In [70]:
#Generate map

#KC_WA_map.save('King_County_WA_map.html')
#IFrame('King_County_WA_map.html', width=700, height=450)

### Using Datapane to Publish

In [54]:
import datapane as dp 

In [55]:
report = dp.Report(dp.Plot(KC_WA_map) ) #Create a report

In [56]:
report.publish(name='KingCountyWA_house_price_map', open=True, visibility='PUBLIC') #Publish the report

Publishing report and associated data - please wait..
Report successfully published at https://datapane.com/u/norleyk/reports/kingcountywa-house-price-map/
